In [1]:
from build123d import *

from jupyter_cadquery import show, show_all,open_viewer, show_clear

from hinge import Hinge



Overwriting auto display for cadquery Workplane and Shape
Overwriting auto display for build123d BuildPart, BuildSketch, BuildLine, ShapeList


In [2]:
#cv = open_viewer("Build123d", anchor="split-bottom")

In [3]:
cv = open_viewer("Build123d", anchor="right")

In [33]:
podnies_karnister = False
otwarta_szuflada = True


# Wymiary szkieletu boxa (mm)
dl = 1810.5
sz = 570.5
wys = 560
profil = 40
profil_8040 = 80 
sklejka = 15
prowadnica = 19

# Wymiary karnistra
dl_k = 360
sz_k = 500
wys_k = 230


# Wymiary Skrzyni
dl_sz = 1100
sz_sz = sz - (2*profil)
wys_sz = wys - profil

# wymiary zlewu

dl_z = 320
sz_z = 260
wys_z = 150
odstep_zlewu_od_konca = 260

dl_sklejki = dl-dl_sz


with BuildPart() as szkielet:
    with Locations((0,-sz/2 + profil/2,0)):
        # Poziome
        with Locations((0, 0, profil/2), (0, sz - profil, profil/2)):
            Box(dl-(2*profil), profil, profil_8040)
        with Locations((0, 0, wys - profil), (0, sz - profil, wys - profil)):
            Box(dl-(2*profil), profil, profil)
        # Pionowe
        with Locations((dl/2-(profil/2),0,wys/2-(profil/2)),(dl/2-(profil/2),sz-(profil),wys/2-(profil/2))):
            Box(profil,profil,wys)
        with Locations((-dl/2+(profil/2),0,wys/2-(profil/2)),(-dl/2+(profil/2),sz-(profil),wys/2-(profil/2))):
            Box(profil,profil,wys)
        # Boczne
        with Locations((dl/2-(profil/2),sz/2-(profil/2),0),(dl/2-(profil/2),sz/2-(profil/2),wys-(profil))):
            Box(profil,sz-(2*profil),profil)
    # sklejka pod karnister
    with Locations((dl/2-dl_sklejki/2,0,0)):
        Box(dl_sklejki,sz,sklejka)



if podnies_karnister == True:
    podnies_karnister = 600
else: 
    podnies_karnister = wys_k/2 + profil/2 + sklejka

with BuildPart() as karnister:
    with Locations((dl/2-dl_k/2-profil,0,podnies_karnister)):
        Box(dl_k,sz_k,wys_k)
    
karnister.part.color = Color("Blue")



if otwarta_szuflada == True:
    szuflada_stan = (-dl/2+dl_sz/2-dl_sz,0,wys/2-profil+15)
else:
    szuflada_stan = (-dl/2+dl_sz/2,0,wys/2-profil+15)
    

with BuildPart() as szuflada:
    with Locations(szuflada_stan):
        Box(dl_sz,sz_sz-(2*prowadnica),wys_sz)
        offset(amount=-15, openings=szuflada.faces().filter_by(Axis.Z)[-1])
        if otwarta_szuflada == True:
            with Locations((-dl_sz/4,45.960,wys_sz/2+154.68)):
                Box(dl_sz/2,sz_sz-2*prowadnica,sklejka, rotation=(-45,0,0))
        else: 
            with Locations((-dl_sz/4,0,wys_sz/2)):
                Box(dl_sz/2,sz_sz-2*prowadnica,sklejka)
        
        with Locations((dl_sz/4,0,wys_sz/2)):
            Box(dl_sz/2,sz_sz-2*prowadnica,sklejka)
            
with BuildPart() as wyciecie:
    with Locations(szuflada_stan):
        with Locations((dl_sz/2 - sz_z/2 - odstep_zlewu_od_konca ,0,wys_sz/2-wys_z/2-sklejka/2+1)):
            Box(sz_z,dl_z,wys_z)
    to_edges = wyciecie.edges().filter_by(Axis.Z)
    fillet(to_edges,radius=20)


with BuildPart() as zlew:
    with Locations(szuflada_stan):
        with Locations((dl_sz/2 - sz_z/2 - odstep_zlewu_od_konca ,0,wys_sz/2-wys_z/2-sklejka/2+1)):
            Box(sz_z,dl_z,wys_z)
            # with Locations(zlew.faces().last):
            #     Hole(10)
            offset(amount=-10,openings=zlew.part.faces().filter_by(Axis.Z)[-1])
            test = zlew.faces().last
            with Locations((0,dl_z/2-50,0)):
                Hole(20)
    to_edges = zlew.edges().filter_by(Axis.Z)
    fillet(to_edges,radius=10)




with BuildPart() as razem:
    add(szkielet)
    add(szuflada)
    add(karnister)
    with Locations((0,0,sklejka)):
        add(wyciecie,mode=Mode.SUBTRACT)
        add(zlew)



# with BuildPart() as model:
#     add(Hinge(20, 40, 6, 2, 3,False))

# show(model.part)



# render_part(my_part.part)  # jeśli używasz jupyter + ocp_vscode
      


# show(szuflada)
# show_all()
show(razem)
# show(zlew,test)

+
